In [1]:
# The code was removed by Watson Studio for sharing.

#### Install the necessary package.

In [2]:
!pip install watson-developer-cloud==1.5
!pip install --user ipython-sql 
!pip install --user ibm_db 
!pip install --user ibm_db_sa
!pip install matplotlib

#### Import the necessary libraries

In [3]:
import requests
import urllib.request
import time
import datetime
import csv
import re
import unicodedata
import ibm_db
from bs4 import BeautifulSoup
import pandas as pd 

#### I've pre-defined some redundant functions here so as to reduce the complexity and size of the code

In [4]:
#function to check if we have access to the website
def access_to_server(a):
    if(access.status_code == 200):
        print("Access to PlaneCrashInfo.com: Granted")
    else:
        print("Access to PlaneCrashInfo.com: Denied")
        
#function to pause for a little so that the website server does not flag us as a spammer
def take_a_break():
    time.sleep(0.1)      #we pause for 3 seconds

#function to access the website
def access_website(url):
    access = None
    access = requests.get(url,timeout=10)
    return access   

def get_data(search_string, regex):
    pattern = re.compile(regex)
    matches = pattern.finditer(search_string)

    for match in matches:
        match = match.span()

    span = search_string[match[0]:match[1]]
    return span

#predefine a dataframe to store out clean data
headers = ['Date','Time','Location','Operator','Flight#','Route','AC Type','Registration','cn/ln','Total Aboard','Passengers Aboard','Crew Aboard','Total Fatalities','Passenger Fatalities','Crew Fatalities','Ground','Summary']
df = pd.DataFrame(headers)
clean_data= df.T

#### Next, we set the url to the Plane Crash Info website and access the site with our requests library. We also set the base url to create a dictionary with years as the key.

In [5]:
base_url = "http://www.planecrashinfo.com"
access = requests.get('http://www.planecrashinfo.com/database.htm')
access_to_server(access)
source = BeautifulSoup(access.text, 'html.parser')

Access to PlaneCrashInfo.com: Granted


 #### Here we build a dictionary with the url stores as the value and the year as the key

In [6]:
a_tags = source.find_all("a")
years = {a.text.strip(): {"url": base_url + a["href"] if a["href"][0] == "/" else base_url + "/" + a["href"]} for a in a_tags if a.text.strip().isdigit()}

#### Here we pause for a little to avoid getting flagged as a spammer.

In [7]:
take_a_break()

#### Now we start collecting the unstructured data

In [8]:
done = 0
for year, database in years.items():       #first we loop for each year from 1920 until 2019
    print(year)
    #if year == '1925':
    #    break
    take_a_break()
    response_year = access_website(database["url"])
    access_to_server(response_year)
    parser_year = BeautifulSoup(response_year.content, 'html.parser')
    a_tags2 = parser_year.find_all("a")
    a_tags2 = [a for a in a_tags2 if "Return to Home" not in a.text]
    for a in a_tags2:
            # request to crash detail page
            response_crash = access_website(base_url + "/" + year + a["href"] if a["href"][0] == "/" else base_url + "/" + year + "/" + a["href"])
            if (response_crash.status_code == 404):
                continue
            parser_crash = BeautifulSoup(response_crash.content, 'html.parser')
            tr_tags = parser_crash.find_all("tr")
            tr_tags = tr_tags[1:]

            database = [tr.find_all("td")[1].text.strip() for tr in tr_tags]  
            x = database
            #Splitting the data in the aboard row
            aboard_row = x[9]
            #remove \xa0 from the string
            aboard_row = unicodedata.normalize("NFKD", aboard_row)
            #remove duplicate spaces from the string
            aboard_row = re.sub(' +', ' ',aboard_row)
            #split the string to extract the data easily
            split_aboard_row = aboard_row.split(" ")
            #find the total number of people aboard
            total_aboard = split_aboard_row[0]
            #find the total number of passengers aboard
            passengers_aboard = split_aboard_row[1]
            passengers_aboard = passengers_aboard[-1]
            #find the total number of crew members aboard
            crew_aboard = split_aboard_row[2]
            crew_aboard = crew_aboard[-2]

            #Splitting the data in the fatalities row
            fatalities_row = x[10]
            #remove \xa0 from the string
            fatalities_row = unicodedata.normalize("NFKD", fatalities_row)
            #remove duplicate spaces from the string
            fatalities_row = re.sub(' +', ' ',fatalities_row)
            #split the string to extract the data easily
            split_fatalities_row = fatalities_row.split(" ")
            #find the total number of fatalities
            total_fatalities = split_fatalities_row[0]
            #find the total number of passenger fatalities
            passenger_fatalities = split_fatalities_row[1]
            passenger_fatalities = passenger_fatalities[-1]
            #find the total number of crew fatalities
            crew_fatalities = split_fatalities_row[2]
            crew_fatalities = crew_fatalities[-2]

            #save data for reorganization
            ground = x[11]
            summary = x[12]
            x[9] = total_aboard
            x[10] = passengers_aboard
            x[11] = crew_aboard
            x[12] = total_fatalities

            u= [passenger_fatalities, crew_fatalities, ground, summary]
            x.extend(u)
            df1 = pd.DataFrame(x) 
            q= df1.T
            clean_data = clean_data.append(q, ignore_index=True, sort=False)

1920
Access to PlaneCrashInfo.com: Granted
1921
Access to PlaneCrashInfo.com: Granted
1922
Access to PlaneCrashInfo.com: Granted
1923
Access to PlaneCrashInfo.com: Granted
1924
Access to PlaneCrashInfo.com: Granted
1925
Access to PlaneCrashInfo.com: Granted
1926
Access to PlaneCrashInfo.com: Granted
1927
Access to PlaneCrashInfo.com: Granted
1928
Access to PlaneCrashInfo.com: Granted
1929
Access to PlaneCrashInfo.com: Granted
1930
Access to PlaneCrashInfo.com: Granted
1931
Access to PlaneCrashInfo.com: Granted
1932
Access to PlaneCrashInfo.com: Granted
1933
Access to PlaneCrashInfo.com: Granted
1934
Access to PlaneCrashInfo.com: Granted
1935
Access to PlaneCrashInfo.com: Granted
1936
Access to PlaneCrashInfo.com: Granted
1937
Access to PlaneCrashInfo.com: Granted
1938
Access to PlaneCrashInfo.com: Granted
1939
Access to PlaneCrashInfo.com: Granted
1940
Access to PlaneCrashInfo.com: Granted
1941
Access to PlaneCrashInfo.com: Granted
1942
Access to PlaneCrashInfo.com: Granted
1943
Access

In [9]:
data_copy = clean_data
data_copy

0     1                                             2   \
0                   Date  Time                                      Location   
1     September 17, 1908  1718                           Fort Myer, Virginia   
2     September 07, 1909     ?                       Juvisy-sur-Orge, France   
3          July 12, 1912  0630                     Atlantic City, New Jersey   
4        August 06, 1913     ?            Victoria, British Columbia, Canada   
5     September 09, 1913  1830                            Over the North Sea   
6       October 17, 1913  1030                    Near Johannisthal, Germany   
7         March 05, 1915  0100                               Tienen, Belgium   
8     September 03, 1915  1520                         Off Cuxhaven, Germany   
9          July 28, 1916     ?                         Near Jambol, Bulgeria   
10    September 24, 1916  0100                           Billericay, England   
11      October 01, 1916  2345                          Potters Bar, England   
12     November 21, 1916     ?                                Mainz, Germany   
13     November 28, 1916  2345                  Off West Hartlepool, England   
14        March 04, 1917     ?                            Near Gent, Belgium   
15        March 30, 1917     ?                          Off Northern Germany   
16          May 14, 1917  0515                  Near Texel Island, North Sea   
17         June 14, 1917  0845                Off Vlieland Island, North Sea   
18         June 17, 1917     ?                        Near Yarmouth, England   
19       August 21, 1917  0700                           Off western Denmark   
20      October 20, 1917  0745                        Near Luneville, France   
21        April 07, 1918  2130                        Over the Mediterranean   
22          May 10, 1918     ?                 Off Helgoland Island, Germany   
23       August 11, 1918  1000                     Ameland Island, North Sea   
24     December 16, 1918     ?                         Elizabeth, New Jersey   
25          May 25, 1919     ?                               Cleveland, Ohio   
26         July 19, 1919     ?                         Dix Run, Pennsylvania   
27         July 21, 1919  1655                             Chicago, Illinois   
28       August 02, 1919     ?                                 Verona, Italy   
29      October 02, 1919     ?                            Newcastle, England   
...                  ...   ...                                           ...   
4936  September 30, 2017  0730                          Near Kinshasa, Congo   
4937    October 12, 2017  1715                            Near Cuílo, Angola   
4938    October 14, 2017  0830                          Abidjan, Ivory Coast   
4939   November 15, 2017  0800                            Empakaai, Tanzania   
4940   December 13, 2017  1815                Near Fond-du-Lac, Saskatchewan   
4941   December 31, 2017  1216                      Punta Islita, Costa Rica   
4942    January 29, 2018     ?  Zhengchang, Suiyang County, Guizhou Province   
4943   February 10, 2018  1731                         Grand Canyon, Arizona   
4944   February 11, 2018  1431                              Argunovo, Russia   
4945   February 18, 2018  0932                        Kohangan village, Iran   
4946      March 06, 2018  1451                                Latakia, Syria   
4947      March 11, 2018  1908                            New York, New York   
4948      March 12, 2018  1415                              Kathmandu, Nepal   
4949      April 11, 2018  0800                          Boufarik AB, Algeria   
4950      April 17, 2018  1004              NW of Philadelphia, Pennsylvania   
4951        May 02, 2018  1130                       Port Wentworth, Georgia   
4952        May 18, 2018  1208                                  Havana, Cuba   
4953       July 10, 2018  0744                        Pretoria, South Africa   
4954     August 04, 20

In [10]:
#Save the dataframe as a CSV to Object Storage
#Commented out after saving once. 
project.save_data(data=data_copy.to_csv(index=False),file_name='planecrashinfo_data1711.csv',overwrite=True)

#### Saving the dataframe as CSV file, I loaded it into IBM db2 database as backup and to allow future access. Below is just a test code to access that SQL databse table. This test code has been used again in the other Jupyter notebooks for the explolatory data analysis. 

In [11]:
#perform simplified database access using SQL "magic"
%load_ext sql
# %sql ibm_db_sa://my-username:my-password@dashdb-txn-sbox-yp-dal09-03.services.dal.bluemix.net:50000/BLUDB
#the cell after this one is hidden because it contains senstive information that provides access to my IBM Cloud account. The code is similar to the line above except for the username and password.

In [12]:
# The code was removed by Watson Studio for sharing.

'Connected: bfc60487@BLUDB'

In [13]:
%sql select * from PlaneCrashInfoDatabase

 * ibm_db_sa://bfc60487:***@dashdb-txn-sbox-yp-dal09-04.services.dal.bluemix.net:50000/BLUDB
Done.


[('17-Sep-08', '1718', 'Fort Myer, Virginia', 'Military - U.S. Army', '?', 'Demonstration', 'Wright Flyer III', '?', '1', '2', '1', '1', '1', '1', '0', '0', 'During a demonstration flight, a U.S. Army flyer flown by Orville Wright nose-dived into the ground from a height of approximately 75 feet, killing L ... (214 characters truncated) ...  of control of the aircraft.  Orville Wright suffered broken ribs, pelvis and a leg.  Selfridge suffered a crushed skull and died a short time later.'),
 ('07-Sep-09', '?', 'Juvisy-sur-Orge, France', '?', '?', 'Air show', 'Wright Byplane', 'SC1', '?', '1', '0', '1', '1', '0', '0', '0', 'Eugene Lefebvre was the first pilot to ever be killed in an air accident, after his controls jambed while flying in an air show.'),
 ('12-Jul-12', '630', 'Atlantic City, New Jersey', 'Military - U.S. Navy', '?', 'Test flight', 'Dirigible', '?', '?', '5', '0', '5', '5', '0', '5', '0', 'First U.S. dirigible Akron exploded just offshore at an altitude of 1,000 ft. during a test flight.'),
 ('06-Aug-13', '?', 'Victoria, British Columbia, Canada', 'Private', '?', '?', 'Curtiss seaplane', '?', '?', '1', '0', '1', '1', '0', '1', '0', 'The first fatal airplane accident in Canada occurred when American barnstormer, John M. Bryant, California aviator was killed.'),
 ('09-Sep-13', '1830', 'Over the North Sea', 'Military - German Navy', '?', '?', 'Zeppelin L-1 (airship)', '?', '?', '20', '?', '?', '14', '?', '?', '0', 'The airship flew into a thunderstorm and encountered a severe downdraft crashing 20 miles north of Helgoland Island into the sea. The ship broke in two and the control car immediately sank drowning its occupants.'),
 ('17-Oct-13', '1030', 'Near Johannisthal, Germany', 'Military - German Navy', '?', '?', 'Zeppelin L-2 (airship)', '?', '?', '30', '?', '?', '30', '?', '?', '0', 'Hydrogen gas which was being vented was sucked into the forward engine and ignited causing the airship to explode and burn at 3,000 ft..'),
 ('05-Mar-15', '100', 'Tienen, Belgium', 'Military - German Navy', '?', '?', 'Zeppelin L-8 (airship)', '?', '?', '41', '?', '?', '21', '?', '?', '0', 'Crashed into trees while attempting to land after being shot down by British and French aircraft.'),
 ('03-Sep-15', '1520', 'Off Cuxhaven, Germany', 'Military - German Navy', '?', '?', 'Zeppelin L-10 (airship)', '?', '?', '19', '?', '?', '19', '?', '?', '0', 'Exploded and burned near Neuwerk Island,  when hydrogen gas, being vented, was ignited by lightning.'),
 ('28-Jul-16', '?', 'Near Jambol, Bulgeria', 'Military - German Army', '?', '?', 'Schutte-Lanz S-L-10 (airship)', '?', '?', '20', '?', '?', '20', '?', '?', '0', 'Crashed near the Black Sea, cause unknown.'),
 ('24-Sep-16', '100', 'Billericay, England', 'Military - German Navy', '?', '?', 'Zeppelin L-32 (airship)', '?', '?', '22', '?', '?', '22', '?', '?', '0', 'Shot down by British aircraft crashing in flames.'),
 ('01-Oct-16', '2345', 'Potters Bar, England', 'Military - German Navy', '?', '?', 'Zeppelin L-31 (airship)', '?', '?', '19', '0', '9', '19', '0', '9', '0', 'Shot down in flames by the British 39th Home Defence Squadron.'),
 ('21-Nov-16', '?', 'Mainz, Germany', 'Military - German Army', '?', '?', 'Super Zeppelin (airship)', '?', '?', '28', '?', '?', '27', '?', '?', '0', 'Crashed in a storm.'),
 ('28-Nov-16', '2345', 'Off West Hartlepool, England', 'Military - German Navy', '?', '?', 'Zeppelin L-34 (airship)', '?', '?', '20', '?', '?', '20', '?', '?', '0', 'Shot down by British anti-aircraft fire and aircraft and crashed into the North Sea.'),
 ('04-Mar-17', '?', 'Near Gent, Belgium', 'Military - German Army', '?', '?', 'Airship', '?', '?', '20', '?', '?', '20', '?', '?', '0', 'Caught fire and crashed.'),
 ('30-Mar-17', '?', 'Off Northern Germany', 'Military - German Navy', '?', '?', 'Schutte-Lanz S-L-9 (airship)', '?', '?', '23', '?', '?', '23', '?', '?', '0', 'Struck by lightning and crashed into the Baltic Sea.'),
 ('14-May-17', '515', 'Near Texel Island, North Sea', 'Military - G

# Data Analysis

In [14]:
#just another copy of data
crash_data = %sql select * from PlaneCrashInfoDatabase

 * ibm_db_sa://bfc60487:***@dashdb-txn-sbox-yp-dal09-04.services.dal.bluemix.net:50000/BLUDB
Done.


In [15]:
# importing all necessery modules 
import matplotlib.pyplot as plt
import scipy as sp
import numpy as np

In [16]:
cr = crash_data

In [17]:
cr2 = data_copy
#cr2[0]

UsageError: Line magic function `%brunel` not found.


In [18]:
data_copy[16]

0                                                 Summary
1       During a demonstration flight, a U.S. Army fly...
2       Eugene Lefebvre was the first pilot to ever be...
3       First U.S. dirigible Akron exploded just offsh...
4       The first fatal airplane accident in Canada oc...
5       The airship flew into a thunderstorm and encou...
6       Hydrogen gas which was being vented was sucked...
7       Crashed into trees while attempting to land af...
8       Exploded and burned near Neuwerk Island,  when...
9              Crashed near the Black Sea, cause unknown.
10      Shot down by British aircraft crashing in flames.
11      Shot down in flames by the British 39th Home D...
12                                    Crashed in a storm.
13      Shot down by British anti-aircraft fire and ai...
14                               Caught fire and crashed.
15      Struck by lightning and crashed into the Balti...
16      Crashed into the sea from an altitude of 3,000...
17            